In [9]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import csv


from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import csv

# CSVファイルの保存設定
output_file = "search_results.csv"

# WebDriverを初期化
driver = webdriver.Chrome()  # 必要に応じてChromeDriverを設定


In [10]:
def fetch_clinical_trials(disease_name="", freeword=""):
    """
    指定された対象疾患名およびフリーワード検索に基づいてjRCTから臨床試験情報を取得します。

    Args:
        disease_name (str): 対象疾患名（例: "がん 神経膠腫 骨髄腫"）
        freeword (str): フリーワード検索（例: "免疫療法"）

    Returns:
        list: 検索結果のリスト（[試験ID, タイトル, 対象疾患, 進捗状況, 日付, リンク]）
    """
    # WebDriverを初期化
    driver = webdriver.Chrome()  # 必要に応じてChromeDriverを設定

    all_results = []

    try:
        # jRCTの検索ページにアクセス
        driver.get("https://jrct.niph.go.jp/search")

        # 対象疾患名を入力
        if disease_name:
            disease_field = WebDriverWait(driver, 10).until(
                EC.presence_of_element_located((By.ID, "reg-plobrem-1"))
            )
            disease_field.send_keys(disease_name)

            # 対象疾患名の条件を「or」に設定
            condition_select = driver.find_element(By.ID, "reg-plobrem-type")
            condition_select.find_element(By.CSS_SELECTOR, "option[value='1']").click()

        # フリーワード検索を入力
        if freeword:
            freeword_field = WebDriverWait(driver, 10).until(
                EC.presence_of_element_located((By.ID, "demo-1"))
            )
            freeword_field.send_keys(freeword)

            # フリーワード検索の条件を「or」に設定
            condition_select = driver.find_element(By.ID, "others")
            condition_select.find_element(By.CSS_SELECTOR, "option[value='1']").click()

        # 募集中を選択
        recruitment_checkbox = driver.find_element(By.ID, "reg-recruitment-2")
        recruitment_checkbox.click()

        # 検索ボタンをクリック
        search_button = driver.find_element(By.NAME, "button_type")
        search_button.click()

        # ページネーション対応ループ
        while True:
            # 現在のページの結果がロードされるのを待機
            WebDriverWait(driver, 10).until(
                EC.presence_of_element_located((By.CSS_SELECTOR, "table tbody tr"))
            )

            # 現在のページの結果を取得
            rows = driver.find_elements(By.CSS_SELECTOR, "table tbody tr")
            for row in rows:
                columns = row.find_elements(By.TAG_NAME, "td")
                if len(columns) > 4:
                    # 試験情報をリストに追加
                    trial_id = columns[0].text
                    title = columns[1].text
                    condition = columns[2].text
                    status = columns[3].text
                    date = columns[4].text

                    # リンクを取得（エラー処理を追加）
                    try:
                        link = columns[1].find_element(By.TAG_NAME, "a").get_attribute("href")
                    except Exception as e:
                        link = "リンク取得エラー"

                    all_results.append([trial_id, title, condition, status, date, link])

            # ページネーションの確認
            try:
                current_page = driver.find_element(By.CSS_SELECTOR, "ul.pagination li.active").text
                print(f"{current_page} ページ目を処理しました。")
            except Exception:
                print("ページネーションが存在しません。全ての結果を取得しました。")
                break

            # 次ページボタンのリストを取得
            pagination_buttons = driver.find_elements(By.CSS_SELECTOR, "ul.pagination li a")
            next_button = None
            for button in pagination_buttons:
                if button.text.isdigit() and int(button.text) > int(current_page):
                    next_button = button
                    break

            if next_button:
                next_button.click()
                WebDriverWait(driver, 10).until(EC.staleness_of(rows[0]))  # ページが変わるまで待機
            else:
                print("次のページはありません。全ての結果を取得しました。")
                break

    finally:
        # ブラウザを閉じる
        driver.quit()

    return all_results


def create_dataframe_from_urls(urls):
    """
    URLのリストを受け取り、pandas DataFrameを作成します。
    """
    
    all_data = []

    for url in urls:
        print(f"Processing URL: {url}")
        # 各メソッドを使ってデータを取得
        purpose = scrape_study_purpose(url)
        design_details = scrape_jrct_details_with_english(url)
        additional_details = scrape_jrct_details(url)

        # 統合する
        data = {"研究・治験の目的": purpose, **design_details, **additional_details}
        all_data.append(data)

    # pandas DataFrameに変換
    return pd.DataFrame(all_data)

In [11]:
import pandas as pd
import requests
from bs4 import BeautifulSoup

def scrape_study_purpose(url):
    """
    指定されたjRCT URLから研究・治験の目的を抽出します。
    """
    response = requests.get(url)
    response.raise_for_status()
    soup = BeautifulSoup(response.text, 'html.parser')

    # "研究・治験の目的" を特定
    purpose_label = soup.find('label', text='研究・治験の目的')
    if purpose_label:
        # "研究・治験の目的" に対応するデータを取得
        purpose_td = purpose_label.find_parent('th').find_next_sibling('td')
        if purpose_td:
            return purpose_td.text.strip()

    return None


def scrape_jrct_details_with_english(url):
    """
    指定されたjRCT URLから試験デザイン情報（日本語と英語の両方）を抽出します。
    """
    response = requests.get(url)
    response.raise_for_status()
    soup = BeautifulSoup(response.text, 'html.parser')

    data = {"URL": url}

    # 試験デザイン項目（日本語と英語をペアで取得）
    design_labels = [
        ('試験の種類', 'Study Type'),
        ('無作為化', 'allocation'),
        ('盲検化', 'masking'),
        ('対照', 'control'),
        ('割付け', 'assignment'),
        ('研究目的', 'purpose')
    ]

    for label_jp, label_en in design_labels:
        label = soup.find('label', string=lambda text: text and label_jp in text)
        if label:
            # 日本語部分のtd
            td_jp = label.find_parent('th').find_next_sibling('td')
            # 英語部分のtd（次のtd要素）
            td_en = td_jp.find_next_sibling('td') if td_jp else None

            # データに日本語と英語を追加
            data[label_jp] = td_jp.text.strip() if td_jp else None
            data[label_en] = td_en.text.strip() if td_en else None

    return data


def scrape_jrct_details(url):
    """
    jRCTの指定URLから、必要な情報を抽出します。
    """
    response = requests.get(url)
    response.raise_for_status()
    soup = BeautifulSoup(response.text, 'html.parser')

    data = {"URL": url}

    # 抽出項目とラベルの対応
    labels = [
        ('主たる選択基準', 'Inclusion Criteria'),
        ('主たる除外基準', 'Exclusion Criteria'),
        ('年齢下限', 'Age Minimum'),
        ('年齢上限', 'Age Maximum'),
        ('性別', 'Gender'),
        ('中止基準', 'Discontinuation Criteria'),
        ('対象疾患キーワード', 'Keyword'),
        ('介入の内容', 'Intervention(s)')
    ]

    for label_jp, label_en in labels:
        # 日本語ラベルを検索
        label = soup.find('label', string=lambda text: text and label_jp in text)
        if label:
            # 日本語部分のデータ
            td_jp = label.find_parent('th').find_next_sibling('td')
            # 英語部分のデータ
            td_en = td_jp.find_next_sibling('td') if td_jp else None

            # データに追加
            data[label_jp] = td_jp.decode_contents().strip().replace('<br/>', '\n') if td_jp else None
            data[label_en] = td_en.decode_contents().strip().replace('<br/>', '\n') if td_en else None

    return data


def extract_jrct_links(results):
    """
    fetch_clinical_trialsの結果からjRCT-Noを抽出し、詳細リンクを作成する。

    Args:
        results (list): fetch_clinical_trialsから得られる結果リスト

    Returns:
        list: jRCTの詳細ページリンクリスト
    """
    base_url = "https://jrct.niph.go.jp/latest-detail/"
    links = []
    for result in results:
        if len(result) > 0:
            jrct_no = result[0]  # jRCT-Noは結果リストの最初の要素
            links.append(base_url + jrct_no)
    return links


def create_dataframe_from_urls(urls):
    """
    URLのリストを受け取り、pandas DataFrameを作成します。
    """
    all_data = []

    for url in urls:
        print(f"Processing URL: {url}")
        # 各メソッドを使ってデータを取得
        purpose = scrape_study_purpose(url)
        design_details = scrape_jrct_details_with_english(url)
        additional_details = scrape_jrct_details(url)

        # 統合する
        data = {"研究・治験の目的": purpose, **design_details, **additional_details}
        all_data.append(data)

    # pandas DataFrameに変換
    return pd.DataFrame(all_data)

def reorder_columns(df):
    """
    DataFrame の列を日本語の列を前半に、英語の列を後半に並び替える。
    """
    # 日本語と英語の列を分ける
    jp_columns = [col for col in df.columns if all(ord(c) < 128 for c in col) is False]  # 非 ASCII（日本語）文字列を含む列
    en_columns = [col for col in df.columns if col not in jp_columns]  # 残りの列を英語と仮定

    # 日本語列 + 英語列の順序で整列
    ordered_columns = jp_columns + en_columns

    # 列を並び替えた DataFrame を返す
    return df[ordered_columns]

In [12]:
# WebDriverを初期化
driver = webdriver.Chrome()  # 必要に応じてChromeDriverを設定

# fetch_clinical_trialsを使って検索結果を取得
results = fetch_clinical_trials(disease_name="神経膠腫 骨髄腫", freeword="")

ページネーションが存在しません。全ての結果を取得しました。


In [13]:
    # jRCT詳細リンクを作成
jrct_links = extract_jrct_links(results)

    # 詳細リンクからデータフレームを作成
df = create_dataframe_from_urls(jrct_links)

Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2051240141


/var/folders/yw/qz00x75d7kb98f7vm8dkhkvw0000gn/T/ipykernel_40777/81950631.py:14: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  purpose_label = soup.find('label', text='研究・治験の目的')


Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2051240121
Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT1031240239
Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2041240056
Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2021240013
Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2031240090
Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2031240014
Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2041240003
Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2031230660
Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2021230055
Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2061230084
Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2071230097
Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2071230095
Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2011230049
Processing URL: https://jrct.niph.go.jp/latest-detail/jRCT2051230108
Processing URL: https://jrct.niph.

HTTPError: 403 Client Error: Forbidden for url: https://jrct.niph.go.jp/latest-detail/jRCTs031200320

In [20]:
# 整列後の DataFrame を作成
sorted_df = reorder_columns(df)

In [25]:
sorted_df['JRCT ID'] = [result[0] for result in results]
sorted_df['Title'] = [result[1] for result in results]

/var/folders/yw/qz00x75d7kb98f7vm8dkhkvw0000gn/T/ipykernel_36648/2325933109.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sorted_df['JRCT ID'] = [result[0] for result in results]
/var/folders/yw/qz00x75d7kb98f7vm8dkhkvw0000gn/T/ipykernel_36648/2325933109.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sorted_df['Title'] = [result[1] for result in results]


In [27]:
new_order = ["JRCT ID", "Title"] + [col for col in sorted_df.columns if col not in ["JRCT ID", "Title"]]

In [28]:
sorted_df = sorted_df[new_order]

In [29]:
sorted_df

JRCT ID                                              Title  \
0   jRCT2051240141  新たに診断され放射線療法を完了したH3 K27M変異を有するびまん性神経膠腫の治療のためのO...   
1   jRCT2051240121  放射線療法後の悪性神経膠腫の小児および若年成人を対象に、アベマシクリブ＋テモゾロミドとテモゾ...   
2   jRCT1031240239  JCOG2303: 可及的摘出されたIDH変異型星細胞腫の術後化学放射線療法に対する待機化学...   
3   jRCT2041240056  [M23-001] 再発性又は難治性多発性骨髄腫患者を対象にABBV-383 を皮下投与する...   
4   jRCT2021240013  ノバルティスが実施した過去のサバトリマブ（MBG453）の試験を完了し，サバトリマブの継続投...   
5   jRCT2031240090  再発悪性神経膠腫に対する治療用放射性薬剤64Cu-ATSMの有効性を検証するランダム化比較医...   
6   jRCT2031240014  自家幹細胞移植に非適応又は初回治療として自家幹細胞移植を予定していない未治療の多発性骨髄腫患...   
7   jRCT2041240003  再発又は難治性の多発性骨髄腫患者を対象に、AZD0305を単剤療法又は抗がん剤との併用療法と...   
8   jRCT2031230660  再発又は難治性多発性骨髄腫患者を対象とした，単剤療法としてのCevostamab及びCevo...   
9   jRCT2021230055  CD38 を標的とする前治療を受けた再発／難治性多発性骨髄腫患者を対象とした，エルラナタマブ...   
10  jRCT2061230084  自家幹細胞移植後の奏効が不十分な初発多発性骨髄腫（NDMM）成人患者を対象とした、ideca...   
11  jRCT2071230097  再発又は難治性の多発性骨髄腫（RRMM）患者を対象にMezigdomide（CC-92480...   
12  jRCT2071230095  再発又は難治性の多発性骨髄腫（RRMM）患者を対象にMezigdomide（CC-92480...   
13  jRCT2011230049  未治療多発性骨髄腫を対象とした自家末梢血幹細胞移植後の地固め療法としてIsatuximab､...   
14  jRCT2051230108  再発及び難治性の多発性骨髄腫患者を対象としたBCMA x CD3 T細胞活性化抗体CC-93...   
15  jRCT2051230069  神経膠腫患者に対するロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...   
16  jRCT2031230223  新たに診断された多発性骨髄腫（NDMM）患者を対象として自家幹細胞移植（ASCT）後のibe...   
17  jRCT2051230065  多発性骨髄腫患者を対象として belantamab の単剤療法と他の治療との併用療法の安全性...   
18  jRCT2031230087  再発又は難治性の多発性骨髄腫患者を対象としたREGN5458（抗BCMA ⅹ 抗CD3二重特...   
19  jRCT2032230060  初発IDH野生型低悪性度神経膠腫に対する交流電場腫瘍治療システムの有効性と安全性を検証する多...   
20  jRCT1070230005                          迅速ウイルスPCR法によるウイルス感染症の早期診断   
21  jRCT2031230009  先行する第I、II及びIII相試験完了後も引き続きイサツキシマブに基づく治療によるベネフィッ...   
22  jRCT2031230007  BRAF融合遺伝子陽性の進行・再発の低悪性度神経膠腫または膵癌に対するビニメチニブの第Ⅱ相医...   
23  jRCT2041220125  抗CD38 モノクローナル抗体及びレナリドミドを含む1～3 ラインの前治療歴がある再発又は難...   
24  jRCT2021220036  MAGNETISMM-6：移植非適応の初発多発性骨髄腫患者を対象としてエルラナタマブ（PF-...   
25  jRCT2063220071  移植適応のある初発の多発性骨髄腫被験者を対象としたダラツムマブ，ボルテゾミブ，レナリドミド及...   
26  jRCT2021220022  [M22-947] 再発又は難治性多発性骨髄腫患者を対象とした薬物治療レジメンを併用したAB...   
27  jRCT2033220220  Ciltacabtagene autoleucel の投与を受けた患者を対象とした長期追跡調査試験   
28  jRCT2031220060  自家造血幹細胞移植後の初発多発性骨髄腫患者を対象としてエルラナタマブ（PF 06863135...   
29  jRCTs051220019       再発悪性神経膠腫に対するホウ素中性子捕捉療法で生じる腫瘍局所の早期反応のPETによる探索   
30  jRCT2053220006  製品規格に適合しないIDECABTAGENE VICLEUCELを被験者に投与する拡大アクセ...   
31  jRCT2031210635  再発又は難治性多発性骨髄腫患者を対象としてteclistamabとダラツムマブ皮下投与製剤の...   
32  jRCT2031210607  有効な治療法がない又は他の治療法が適さない再発・難治性多発性骨髄腫患者を対象としたベランタマ...   
33  jRCT2033210469                                     デリタクト注使用成績比較調査   
34  jRCTs071210084  未治療の高齢多発性骨髄腫に対する新規薬剤と自家移植を組み合わせたシークエンス治療を固定期間で...   
35  jRCTs071210074  未治療多発性骨髄腫に対するダラツムマブ、レナリドミドおよびデキサメタゾン療法に治療奏効で層別...   
36  jRCT2031210299                     再発悪性神経膠腫患者を対象としたDSP-0390の第1相試験   
37  jRCT2011210025  造血幹細胞移植の適応とならない初発の多発性骨髄腫患者を対象として，ボルテゾミブ，レナリドミド...   
38  jRCT2051210043  再発又は難治性の多発性骨髄腫（RRMM）患者を対象にiberdomide、ダラツムマブ及びデ...   
39  jRCTs031200320  JCOG1911: 高齢者または移植拒否若年者の未治療多発性骨髄腫患者に対するダラツムマブ＋...   
40  jRCT2033200278  MMG49 抗原陽性の再発・難治性多発性骨髄腫患者を対象に OPC-415 の安全性及び有効...   
41  jRCTs071190010    悪性神経膠腫に対する高圧酸素療法、メマンチン塩酸塩併用放射線化学治療：第Ⅲ相ランダム化比較試験   
42  jRCTs021180010  塩酸ニムスチン(ACNU)を用いたconvection enhanced delivery法...   
43  jRCTs061180085  初発悪性神経膠腫に対する手術、術後放射線治療およびTemozolomide併用の標準治療と、...   
44  jRCTs031180170            初発悪性神経膠腫に対するVEGFR1/2ペプチドワクチンの第I/II相臨床試験   

                                             研究・治験の目的  \
0   H3 K27M変異びまん性神経膠腫を有する被験者を対象に、放射線療法後に投与されたONC20...   
1   放射線療法後の悪性神経膠腫を有する小児および若年成人を対象に、アベマシクリブとテモゾロミドの...   
2   手術で可及的摘出（90%以上の摘出）されたIDH変異型星細胞腫Grade 3を対象に、標準治...   
3     再発又は難治性（R/R）MMの成人患者を対象にABBV-383の安全性及び薬物動態を検討する。   
4               重篤な有害事象（SAE）及び有害事象（AE）を含めて，安全性を評価すること   
5   再発・難治性悪性神経膠腫を対象として、64Cu-diacetyl-bis（N4-methyl...   
6   本研究の目的は，teclistamabとダラツムマブ及びレナリドミドの併用（Tec-DR）並...   
7                                           Treatment   
8   本試験は、再発または難治性の多発性骨髄腫（R/R MM）患者を対象に、Cevostamab単...   
9   再発または難治性多発性骨髄腫患者を対象に，エルラナタマブ単剤投与の有効性，安全性等を標準療法...   
10  自家幹細胞移植後の奏効が不十分なNDMM成